# Prepare Flickr API Batch CSV

In [1]:
%reload_ext autoreload
%autoreload 2

import os
from os.path import join
from glob import glob, iglob
from pathlib import Path
from tqdm import tqdm_notebook as tqdm

import pandas as pd

## IBM DiF clean CSVs

- 2283 files could not be downloaded or accessed in the API
- these images were downloaded, but possibly no longer exist

In [60]:
# flickr api data
fp_in_meta_flickr = '/data_store_hdd/datasets/people/ibm_dif/research/ibm_dif_meta_flickr.csv'

# api query dump
fp_in_flickr_api = '/data_store_hdd/datasets/people/ibm_dif/research/flickr_api_query_dump.csv'

# ibm count data
fp_in_meta_filepaths = '/data_store_hdd/datasets/people/ibm_dif/research/ibm_dif_meta_filepaths.csv'
fp_meta_filepaths_adj = '/data_store_hdd/datasets/people/ibm_dif/research/ibm_dif_meta_filepaths_adj.csv'

In [44]:
df_meta_filepaths = pd.read_csv(fp_in_meta_filepaths)
meta_filepaths = df_meta_filepaths.to_dict('records')
df_meta_flickr = pd.read_csv(fp_in_meta_flickr)
meta_flickr = df_meta_flickr.to_dict('records')
df_flickr_api_dump = pd.read_csv(fp_in_flickr_api)

/home/adam/anaconda3/envs/megapixels/lib/python3.6/site-packages/IPython/core/interactiveshell.py:3020: DtypeWarning: Columns (2,3,10) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [47]:
print(len(df_flickr_api_dump))
print(len(df_flickr_api_dump.drop_duplicates(subset='nsid')))
print(len(df_meta_flickr))
print(len(df_meta_filepaths))
print(len(df_meta_filepaths.drop_duplicates(subset='nsid')))

98155
98155
98153
100438
98154


In [59]:
# drop epmty NSIDs
df_meta_filepaths.drop_duplicates(subset='nsid', inplace=True)

In [61]:
df_meta_filepaths.to_csv(fp_meta_filepaths_adj, index=False)

In [55]:
nsid_filepaths = {}
dupes = []
for meta_filepath in meta_filepaths:
  nsid = meta_filepath['nsid']
  if nsid not in nsid_filepaths.keys():
    nsid_filepaths[nsid] = meta_filepath
  else:
    dupes.append(meta_filepath)

In [56]:
print(len(nsid_filepaths))
print(len(dupes))

98154
2284


In [58]:
for dupe in dupes[:10]:
  print(dupe)

{'filepath': '12537662393_247b2187ee.jpg', 'nsid': nan, 'photo_id': 12537662393, 'url': 'http://farm6.staticflickr.com/5476/12537662393_247b2187ee.jpg'}
{'filepath': '5837222502_29aaf5bb53.jpg', 'nsid': nan, 'photo_id': 5837222502, 'url': 'http://farm4.staticflickr.com/3089/5837222502_29aaf5bb53.jpg'}
{'filepath': '10859466623_4ceb1564dc.jpg', 'nsid': nan, 'photo_id': 10859466623, 'url': 'http://farm6.staticflickr.com/5530/10859466623_4ceb1564dc.jpg'}
{'filepath': '13719567455_fb96dc7ac6.jpg', 'nsid': nan, 'photo_id': 13719567455, 'url': 'http://farm4.staticflickr.com/3718/13719567455_fb96dc7ac6.jpg'}
{'filepath': '3486554266_ca1fc7d99c.jpg', 'nsid': nan, 'photo_id': 3486554266, 'url': 'http://farm4.staticflickr.com/3327/3486554266_ca1fc7d99c.jpg'}
{'filepath': '6168324261_d2fb7bbb60.jpg', 'nsid': nan, 'photo_id': 6168324261, 'url': 'http://farm7.staticflickr.com/6166/6168324261_d2fb7bbb60.jpg'}
{'filepath': '13938295982_0d950feba5.jpg', 'nsid': nan, 'photo_id': 13938295982, 'url': 'ht

In [51]:
print(len(dupes))

100438


In [8]:
print(len(nsid_groups))

98153


In [16]:
fp_ims = glob('/data_store_hdd/datasets/people/ibm_dif/downloads/images/*.jpg')
print(len(fp_ims))

100436


In [18]:
photo_ids = [Path(x).stem.split('_')[0] for x in fp_ims]
print(photo_ids[0])

9314013316


In [45]:
filepath_photo_ids = [int(x['nsid']) for x in meta_flickr]

KeyError: 'photo_id'

In [41]:
# find which photo IDs are no longer accessible
missing_photo_ids = []
for photo_id in tqdm(photo_ids):
  photo_id = int(photo_id)
  if photo_id not in filepath_photo_ids:
    missing_photo_ids.append(photo_id)

In [42]:
print(len(missing_photo_ids))
print(missing_photo_ids[0:10])

0
[]


In [30]:
total = df_flickr_meta['count'].sum()
print(total)

NameError: name 'df_flickr_meta' is not defined

In [ ]:
# load ibm data and create count lookup with photoid
df_ibm_meta = pd.read_csv(fp_in_ibm_meta)
ibm_meta_records = df_ibm_meta.to_dict('records')
count_lookup = {}
for ibm_meta_record in ibm_meta_records:
  photo_id = int(Path(ibm_meta_record['url']).stem.split('_')[0])
  count_lookup[photo_id] = ibm_meta_record['count']

In [ ]:
len(count_lookup)

In [ ]:
results = []

In [ ]:
df_flickr_meta = pd.read_csv(fp_in_flickr_meta, dtype={'count': int, 'username': str, 'sha256': str}).fillna('')
flickr_meta_records = df_flickr_meta.to_dict('records')

In [ ]:
# load flickr data
for flickr_meta_record in flickr_meta_records:
  try:
    nsid = flickr_meta_record['nsid']
    photo_id = int(flickr_meta_record['photo_id'])
    count = count_lookup[photo_id]
  except Exception as e:
    print(f'Error: {e}, {flickr_meta_record}')
    continue
  obj = {
    'photo_id': photo_id,
    'nsid': nsid,
    'count': count 
  }
  results.append(obj)

In [ ]:
df_out = pd.DataFrame.from_dict(results)
df_out.to_csv(fp_out, index=False)

## Create meta count file

In [ ]:
# photo ids and nsids
fp_flickr_api_dump = '/data_store_hdd/datasets/people/ibm_dif/research/flickr_api_query_dump.csv'

# file urls
fp_ibm_urls = '/data_store_hdd/datasets/people/ibm_dif/research/ibm_dif_urls.csv'

# flickr meta
fp_out_filepaths = '/data_store_hdd/datasets/people/ibm_dif/research/ibm_dif_filepaths.csv'

In [ ]:
df_flickr_meta = pd.read_csv(fp_flickr_api_dump)
df_flickr_meta.fillna('', inplace=True)
flickr_metas = df_flickr_meta.to_dict('records')

```
|filepath|nsid|photo_id|url|
```

In [ ]:
photo_id_to_nsid = {}
for flickr_meta in flickr_metas:
  photo_id = flickr_meta.get('photo_id')
  if photo_id:
    photo_id = str(int(photo_id))
    photo_id_to_nsid[photo_id] = flickr_meta['nsid']

In [ ]:
print(list(photo_id_to_nsid.keys())[0:10])

In [ ]:
df_ibm_urls = pd.read_csv(fp_ibm_urls)
ibm_urls = df_ibm_urls.to_dict('records')

In [ ]:
photo_id_to_url = {}
missed = []
for ibm_url in ibm_urls:
  photo_id = str(ibm_url['filepath'].split('_')[0])
  try:
    ibm_url['photo_id'] = photo_id
    ibm_url['nsid'] = photo_id_to_nsid[photo_id]
  except Exception as e:
#     print(e, photo_id)
    missed.append(photo_id)
print(f'missed: {len(missed)}')

In [ ]:
pd.DataFrame.from_dict(ibm_urls).to_csv(fp_out_filepaths, index=False)